This notebook contains details about various commands and techniques that might obscure the main point in the other documents.

# Debugging Nikola

Here are some tips for debugging Nikola when things go wrong.

* Run with pdb support:

  ```bash
  NIKOLA_DEBUG=1 nikola build -v 2 --pdb
  ```
  
  This does not halt some errors though.  You can force Nikola to halt on warnings with 
  
  ```bash
  nikola build --strict
  ```
  
  This will give tracebacks about the warnings that might be hidden.

# Clean Environment

To get as clean an environment as possible, I did the following:

```bash
$ conda create -n blog3 python=3
$ conda activate blog3
$ pip install Nikola

# Trying to run nikola build on my site gave errors requiring
# the following
# ModuleNotFoundError: No module named 'mmf_setup'
# ERROR: Nikola: In order to use this theme, you must install the "jinja2" Python package.
# ERROR: Nikola: In order to build this site (compile ipynb), you must install the "notebook>=4.0.0" Python package.

$ conda install mmf_setup jinja2 notebook

# Now we clean the environment, installing as much as possible with conda
$ conda install pipdeptree
$ pipdeptree | perl -nle'print if m{^\w+}'
```

# Python 2 vs Python 3

As of 2020, Python 2 support has stopped, and all major libraries now support Python 3.  This includes Mercurial as of version 5.2, our main reason for holding back.  Thus, at this point, I strongly recommend starting from Python 3.  The remaining material here is for historical reasons.

Discussions here:

* https://wiki.python.org/moin/Python2orPython3
* https://groups.google.com/a/continuum.io/forum/#!topic/anaconda/WdS85V816rw

One issue is that [mercurial requires Python 2](http://mercurial.selenic.com/wiki/SupportedPythonVersions#Python_3.x_support) and likely will not support Python 3 for some time.  This means that we will have to get users to install Mercurial separately as part of their OS.

Since I often want control of Mercurial, I still would like to install it under conda.  Here is how I do it:

1. Install Miniconda (see below) with ``python=2`` into ``/data/apps/anaconda/bin``.
2. ``conda install mercurial``.  This gives me a working version.
3. ``conda create -n talent2012 python=3 anaconda``.  This is my python 3 working environment.
4. Make sure that ``/data/apps/anaconda/bin`` appears at both the start and end of my path.  For example:

   ```bash
   export PATH="/data/apps/anaconda/bin:$PATH:/data/apps/anaconda/bin/./"
   ```
   
This little trick ensures that when I activate a new environment, the default ``bin`` directory remains on my path after so that ``hg`` can fallback and still work:

```bash
$ . activate talent2015
discarding /data/apps/anaconda/bin from PATH
prepending /data/apps/anaconda/envs/talent2015/bin to PATH
(talent2015) $ echo $PATH
/data/apps/anaconda/envs/talent2015/bin:...:/data/apps/anaconda/bin/./
```

# Conda

* ``conda install`` seems to also do a ``conda update``, so use this in examples if you are not certain the user has installed the package (in which case ``conda update`` will fail).

## Clean Environment (for Developers)

If you are developing code, then it is important to have a clean environment so you don't accidentally depend on packages that you forget to tell the students to install.  This can be done as follows.  (Not everyone needs to add this complication – we just need to make sure that a few people test all the code in a clean environment.)  Here is how I am doing this now (MMF):

1. First I installed a clean version of [Miniconda](http://conda.pydata.org/miniconda.html) based on Python 2 so that I can use mercurial.  This is the minimal package manager without any additional dependencies.  The reason is that any environments you create will have access to the packages installed in the root (default) and I would like to be able to test code *without* the full anaconda distribution.  Since we require the full [Anaconda](https://store.continuum.io/cshop/anaconda/) distribution here, it is fine to install it instead if you don't care about testing your code in clean environment.

   I install mine in a global location ``/data/apps/anaconda``. (This path will appear in examples below.  Modify to match your installation choice.  I believe the default is your home directory ``~/miniconda`` or ``~/anaconda``.)  To use this, you need to add the appropriate directory to your path.  The installer will offer to do this for you but if you customize your startup files, you might need to intervene a little.  Make sure that something like this appears in your ``~/.bash_profile`` or ``~/.bashrc`` file:
   
   ```bash
export PATH="/data/apps/anaconda/bin:$PATH:/data/apps/anaconda/bin/./"
export DYLD_LIBRARY_PATH "/data/apps/anaconda/anaconda/lib:$DYLD_LIBRARY_PATH"
```

   (The library path is useful if you install shared libraries like the [FFTW](http://www.fftw.org) and want to manage them with ``conda``.  *Someone with Linux expertise, please add the appropriate environmental exports for the linux platform.*)
2. Next I create various environments for working with different versions of python, etc.  For this project I do:

   ```bash
   conda create -n py2 python=2
   conda create -n py3 python=3
   conda create -n anaconda2 anaconda
   conda create -n anaconda3 anaconda python=3
   conda create -n talent2015 python=3 anaconda
   ```

   This creates a new full anaconda distribution in the environment named ``talent2015``.  To use this you activate it with one of (requires ``bash`` or ``zsh``):
   
   ```bash
   source activate talent2015
   # OR
   . activate talent2015         # The "." is a shortcut for "source"
   ```

   All this really does is modify your ``PATH`` to point to ``/data/apps/anaconda/envs/talent2015/bin``. When you are finished, you can deactivate this with:
   
   ```bash
   . deactivate
   ```
   


# New Posts

There appears to be no easy way to customize new posts.  In particular, as of version 7.7.6 I tried to modify the template to insert `<!-- TEASER_END -->` after the content.  I traced this to line 141 in `nikola/plugins/compile/ipynb.py` which inserts the `content`.  The actual content is a translated version of "Write your post here." and everything is inserted programatically without any apparent opportunity for customization.

In order to customize this, I use a custom script for starting new posts:

```bash
# Creates a new blog post
function np ()
{
    cd /Users/mforbes/current/website/posts/private_blog/
    . activate blog
    nikola new_post -i  /Users/mforbes/current/website/new_post_content.md
    . activate work
}
```

Then I place the following content in the file `/Users/mforbes/current/website/new_post_content.md`:

```md
![Figure Description](/images/Figure.png)
# Title
Write your post here!
<!-- TEASER_END -->
```

Note: In order for this to work, I needed to make sure that the markdown compiler was not disabled.  To do this, I made sure that in my `conf.py` file, I had at least one reference to markdown (I did this in my pages list:)

```python
...
PAGES = (
    ("pages/*.md", "", "story.tmpl"),
    ("pages/*.rst", "", "story.tmpl"),
    ("pages/*.txt", "", "story.tmpl"),
    ("pages/*.html", "", "story.tmpl"),
)
```